## CS 200: Python Virtual Machine (PVM)


<script language="JavaScript">
    document.write("Last modified: " + document.lastModified)
</script>

Video: <a target=vv href="https://www.youtube.com/watch?v=cSSpnq362Bk">A Bit about Bytes: Understanding Python Bytecode</a> James Bennett, PyCon 2018, 

EBook: <a target=bb href="https://leanpub.com/insidethepythonvirtualmachine">Inside The Python Virtual Machine</a> Obi Ike-Nwosu 

Github: <a target=qq href="https://github.com/python/cpython">github.com/python/cpython</a> source code for Python. <a target=ccc href="https://github.com/python/cpython/blob/main/Python/ceval.c">ceval.c</a>


Python source code is converted to python byte code, which is then executed by the python virtual machine.  The <code>.pyc</code> files contain python byte code.

Python source code goes through the following process:
<ol>
    <li> Lexical analysis. Break the code up into tokens. (See flex in UNIX, <i>nee</i>, lex)
<li> Parsing. Generate a syntactic parse tree. (Like diagramming sentences using parts of speech.) (See bison in UNIX, <i>nee</i>, yacc)
<li> Code generation. Python traverses the code tree and produces a byte code file - usually a .pyc file. (Resides in __pycache__ in Python 3. Take a look.)
<li> Execution. The Python Virtual Machine reads the byte code and executes the instructions.
    </ol>


Some of the modules we use to explore the byte code include:

- <a target=ww href="https://docs.python.org/3/library/dis.html">dis</a> the disassembler.  It can convert python source code to byte code.
- <a target=qw href="https://svn.python.org/projects/python/trunk/Lib/opcode.py">opcode</a> which converts numeric byte codes to symbolic assembler code.  For example, opcode 23 is the assembler instruction, BINARY_ADD
- <a target=rr href="https://docs.python.org/3/library/operator.html">operator module</a> provides function names for standard operators.  For example, < is operator.lt(a,b)

See the local files: <a target=qq href="bytecode.py">bytecode.py</a> and <a target=wer href="pvm.py">pvm.py</a>

In [1]:
import dis
import operator
import opcode

We define a simple function.

In [2]:
def s():
    a = 1
    b = 2
    return (a + b)

In [3]:
s()

3

We check out the attributes of the function.

In [4]:
dir(s)

['__annotations__',
 '__call__',
 '__class__',
 '__closure__',
 '__code__',
 '__defaults__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__get__',
 '__getattribute__',
 '__globals__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__kwdefaults__',
 '__le__',
 '__lt__',
 '__module__',
 '__name__',
 '__ne__',
 '__new__',
 '__qualname__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__']

Now we drill down on the <tt>\_\_code\_\_</tt> attribute.

In [5]:
dir(s.__code__)

['__class__',
 '__delattr__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 'co_argcount',
 'co_cellvars',
 'co_code',
 'co_consts',
 'co_filename',
 'co_firstlineno',
 'co_flags',
 'co_freevars',
 'co_kwonlyargcount',
 'co_lnotab',
 'co_name',
 'co_names',
 'co_nlocals',
 'co_posonlyargcount',
 'co_stacksize',
 'co_varnames',
 'replace']

We define a function, xf(), which will print out the value of the attributes of the \_\_code\_\_ property.

In [6]:
def xf(func, all=False):
    for x in (dir(func.__code__)):
        if all:
            print ("{}:\t{}".format(x, func.__code__.__getattribute__(x)))
        elif x.startswith("co"):
            print ("{}:\t{}".format(x, func.__code__.__getattribute__(x)))

In [7]:
xf(s)

co_argcount:	0
co_cellvars:	()
co_code:	b'd\x01}\x00d\x02}\x01|\x00|\x01\x17\x00S\x00'
co_consts:	(None, 1, 2)
co_filename:	/tmp/ipykernel_2260377/1904000924.py
co_firstlineno:	1
co_flags:	67
co_freevars:	()
co_kwonlyargcount:	0
co_lnotab:	b'\x00\x01\x04\x01\x04\x01'
co_name:	s
co_names:	()
co_nlocals:	2
co_posonlyargcount:	0
co_stacksize:	2
co_varnames:	('a', 'b')


Every time you define a function, Python creates these attributes.  Some are obvious, and others are obscure.  We will start by looking at the co\_code attribute, which is the byte code instructions needed to execute the function.

We define a simple function getbytes(f) to retrieve the bytecodes.

In [8]:
def getbytes(f):
    return f.__code__.co_code

In [9]:
getbytes(s)

b'd\x01}\x00d\x02}\x01|\x00|\x01\x17\x00S\x00'

See <a target=ww href="Hexadecimal.html">Hexadecimal.html</a> for a discussion of hexadecimal byte strings.

We next define a function to print out the individual bytes.

In [10]:
def printbytes(f):
    for b in getbytes(f):
        print (b)

In [11]:
printbytes(s)

100
1
125
0
100
2
125
1
124
0
124
1
23
0
83
0


Some of those bytes are opcodes - that is, assembly language instructions.  The opcode module provides a mapping between bytes and opcodes.

In [12]:
dir(opcode)

['EXTENDED_ARG',
 'HAVE_ARGUMENT',
 '__all__',
 '__builtins__',
 '__cached__',
 '__doc__',
 '__file__',
 '__loader__',
 '__name__',
 '__package__',
 '__spec__',
 'cmp_op',
 'hascompare',
 'hasconst',
 'hasfree',
 'hasjabs',
 'hasjrel',
 'haslocal',
 'hasname',
 'hasnargs',
 'opmap',
 'opname',
 'stack_effect']

In [13]:
opcode.opname

['<0>',
 'POP_TOP',
 'ROT_TWO',
 'ROT_THREE',
 'DUP_TOP',
 'DUP_TOP_TWO',
 'ROT_FOUR',
 '<7>',
 '<8>',
 'NOP',
 'UNARY_POSITIVE',
 'UNARY_NEGATIVE',
 'UNARY_NOT',
 '<13>',
 '<14>',
 'UNARY_INVERT',
 'BINARY_MATRIX_MULTIPLY',
 'INPLACE_MATRIX_MULTIPLY',
 '<18>',
 'BINARY_POWER',
 'BINARY_MULTIPLY',
 '<21>',
 'BINARY_MODULO',
 'BINARY_ADD',
 'BINARY_SUBTRACT',
 'BINARY_SUBSCR',
 'BINARY_FLOOR_DIVIDE',
 'BINARY_TRUE_DIVIDE',
 'INPLACE_FLOOR_DIVIDE',
 'INPLACE_TRUE_DIVIDE',
 '<30>',
 '<31>',
 '<32>',
 '<33>',
 '<34>',
 '<35>',
 '<36>',
 '<37>',
 '<38>',
 '<39>',
 '<40>',
 '<41>',
 '<42>',
 '<43>',
 '<44>',
 '<45>',
 '<46>',
 '<47>',
 'RERAISE',
 'WITH_EXCEPT_START',
 'GET_AITER',
 'GET_ANEXT',
 'BEFORE_ASYNC_WITH',
 '<53>',
 'END_ASYNC_FOR',
 'INPLACE_ADD',
 'INPLACE_SUBTRACT',
 'INPLACE_MULTIPLY',
 '<58>',
 'INPLACE_MODULO',
 'STORE_SUBSCR',
 'DELETE_SUBSCR',
 'BINARY_LSHIFT',
 'BINARY_RSHIFT',
 'BINARY_AND',
 'BINARY_XOR',
 'BINARY_OR',
 'INPLACE_POWER',
 'GET_ITER',
 'GET_YIELD_FROM_ITE

In [14]:
len(opcode.opname)

256

In [15]:
opcode.opname[23]

'BINARY_ADD'

The opcode.opname array maps numbers to opcodes. We define a function <tt>printopcodes(f)</tt> to map these codes for a given function.

In [16]:
def printopcodes(f):
    for b in getbytes(f):
        print ("{}: {}".format(b, opcode.opname[b]))

In [17]:
printopcodes(s)

100: LOAD_CONST
1: POP_TOP
125: STORE_FAST
0: <0>
100: LOAD_CONST
2: ROT_TWO
125: STORE_FAST
1: POP_TOP
124: LOAD_FAST
0: <0>
124: LOAD_FAST
1: POP_TOP
23: BINARY_ADD
0: <0>
83: RETURN_VALUE
0: <0>


The <code>dis</code> module has a <code>dis()</code> function which performs this task, as well as the <code>code\_info()</code> function which provides additional information. 

In [18]:
opcode.opname[23]

'BINARY_ADD'

In [19]:
dis.dis(s)

  2           0 LOAD_CONST               1 (1)
              2 STORE_FAST               0 (a)

  3           4 LOAD_CONST               2 (2)
              6 STORE_FAST               1 (b)

  4           8 LOAD_FAST                0 (a)
             10 LOAD_FAST                1 (b)
             12 BINARY_ADD
             14 RETURN_VALUE


In [20]:
print( dis.code_info(s))

Name:              s
Filename:          /tmp/ipykernel_886261/1904000924.py
Argument count:    0
Positional-only arguments: 0
Kw-only arguments: 0
Number of locals:  2
Stack size:        2
Flags:             OPTIMIZED, NEWLOCALS, NOFREE
Constants:
   0: None
   1: 1
   2: 2
Variable names:
   0: a
   1: b


We combine these in the <code>showme(f)</code> function.

In [21]:
def showme(f):
    dis.dis(f)
    print(dis.code_info(f))    

In [22]:
showme(s)

  2           0 LOAD_CONST               1 (1)
              2 STORE_FAST               0 (a)

  3           4 LOAD_CONST               2 (2)
              6 STORE_FAST               1 (b)

  4           8 LOAD_FAST                0 (a)
             10 LOAD_FAST                1 (b)
             12 BINARY_ADD
             14 RETURN_VALUE
Name:              s
Filename:          /tmp/ipykernel_886261/1904000924.py
Argument count:    0
Positional-only arguments: 0
Kw-only arguments: 0
Number of locals:  2
Stack size:        2
Flags:             OPTIMIZED, NEWLOCALS, NOFREE
Constants:
   0: None
   1: 1
   2: 2
Variable names:
   0: a
   1: b


### PVM-lite

See <a target=qq href="http://aosabook.org/en/500L/a-python-interpreter-written-in-python.html">A Python Interpreter Written in Python</a>

Note that this article was written using an earlier version of Python, 3.4 or so.  In that version, bytecodes used three bytes: one for the opcode and two for the arguments.
After 3.4, Python generated bytecode that used only two bytes per opcode.  That is what we use in this assignment.  You should make the adjustment in the reading.

In [24]:
what_to_execute = {
    "instructions": [("LOAD_VALUE", 0),
                     ("LOAD_VALUE", 1),
                     ("ADD_TWO_VALUES", None),
                     ("PRINT_ANSWER", None)],
    "numbers": [7, 5] }

In [25]:
def s():
    a = 1
    b = 2
    print (a + b)

In [26]:
swhat_to_execute = {
    "instructions": [("LOAD_VALUE", 0),
                     ("STORE_NAME", 0),
                     ("LOAD_VALUE", 1),
                     ("STORE_NAME", 1),
                     ("LOAD_NAME", 0),
                     ("LOAD_NAME", 1),
                     ("ADD_TWO_VALUES", None),
                     ("PRINT_ANSWER", None)],
    "numbers": [1, 2],
    "names": ["a", "b"] }

### The Interpreter

We implement two interpreters in one. They both use a stack to execute the instructions.

- run_code() - which is a simpler, more limited interpreter, with the instructions hard coded.
- execute() - which is more general, allowing the instructions to be other methods in the class.

The latter relies on the <a target=ll href="https://docs.python.org/3/library/functions.html#getattr"><code>getattr(object, name)</code></a> function, which returns the value of the named attribute of the object.

In [27]:
class Interpreter0:
    def __init__(self):
        self.stack = []
        self.environment = {}

    def STORE_NAME(self, name):
        val = self.stack.pop()
        self.environment[name] = val

    def LOAD_NAME(self, name):
        val = self.environment[name]
        self.stack.append(val)

    def LOAD_VALUE(self, number):
        self.stack.append(number)

    def PRINT_ANSWER(self):
        answer = self.stack.pop()
        print (answer)

    def ADD_TWO_VALUES(self):
        first_num = self.stack.pop()
        second_num = self.stack.pop()
        total = first_num + second_num
        self.stack.append(total)

    def run_code(self, what_to_execute):
        instructions = what_to_execute["instructions"]
        for each_step in instructions:
            instruction, argument = each_step
            argument = self.parse_argument(instruction, argument, what_to_execute)
            if instruction == "LOAD_VALUE":
                self.LOAD_VALUE(argument)
            elif instruction == "ADD_TWO_VALUES":
                self.ADD_TWO_VALUES()
            elif instruction == "PRINT_ANSWER":
                self.PRINT_ANSWER()
            elif instruction == "STORE_NAME":
                self.STORE_NAME(argument)
            elif instruction == "LOAD_NAME":
                self.LOAD_NAME(argument)

    def parse_argument(self, instruction, argument, what_to_execute):
        numbers = ["LOAD_VALUE"]
        names = ["LOAD_NAME", "STORE_NAME"]

        if instruction in numbers:
            argument = what_to_execute["numbers"][argument]
        elif instruction in names:
            argument = what_to_execute["names"][argument]
        return argument

    ## stage 2 version of PVM
    ## -------------------------------------------------------------
    def execute(self, what_to_execute):
        instructions = what_to_execute["instructions"]
        for each_step in instructions:
            print (each_step)
            instruction, argument = each_step
            argument = self.parse_argument(instruction, argument, what_to_execute)
            bytecode_method = getattr(self, instruction)
            if argument is None:
                bytecode_method()
            else:
                bytecode_method(argument)

In [28]:
def test():
    interpreter = Interpreter0()
    interpreter.run_code(what_to_execute)

In [29]:
what_to_execute

{'instructions': [('LOAD_VALUE', 0),
  ('LOAD_VALUE', 1),
  ('ADD_TWO_VALUES', None),
  ('PRINT_ANSWER', None)],
 'numbers': [7, 5]}

In [30]:
test()

12


In [31]:
swhat_to_execute

{'instructions': [('LOAD_VALUE', 0),
  ('STORE_NAME', 0),
  ('LOAD_VALUE', 1),
  ('STORE_NAME', 1),
  ('LOAD_NAME', 0),
  ('LOAD_NAME', 1),
  ('ADD_TWO_VALUES', None),
  ('PRINT_ANSWER', None)],
 'numbers': [1, 2],
 'names': ['a', 'b']}

In [32]:
def test2():
    interpreter = Interpreter0()
    interpreter.run_code(swhat_to_execute)

In [33]:
test2()

3


In [34]:
def test3():
    interpreter = Interpreter0()
    interpreter.execute(swhat_to_execute)

In [35]:
test3()

('LOAD_VALUE', 0)
('STORE_NAME', 0)
('LOAD_VALUE', 1)
('STORE_NAME', 1)
('LOAD_NAME', 0)
('LOAD_NAME', 1)
('ADD_TWO_VALUES', None)
('PRINT_ANSWER', None)
3


### hw5: Interpreter: PVM-lite

Following the description in the reading, you will implement 
PVM-lite: A Python Virtual Machine for a subset of Python.  

Included in the subset are:

- constants
- local variables
- arithmetic operators
- comparison operators
- if/then/else
- lists, tuples, sets, dictionaries (maps)
- slices
- unary operators
- inplace operators


Not included are:

- for, while loops
- function calls
- function arguments
- classes
- list comprehensions 
- generators
- global variables
- lambda expressions



The dis module can disassemble a Python function, printing out 
the byte codes for the function.  For example, given:

In [36]:
def s1():
    a = 1
    return a

In [37]:
import dis
dis.dis(s1)

  2           0 LOAD_CONST               1 (1)
              2 STORE_FAST               0 (a)

  3           4 LOAD_FAST                0 (a)
              6 RETURN_VALUE


Write your own version of dis.dis() that produces a dictionary object 
containing the following values:
 
- names: a list of the function's variable names (the .co_varnames attribute)
- consts: a list of the function's constants (the .co_consts attribute)
- code: a list of the function's bytecode (the .co_code attribute)
- instructions: a list of the sequence of instructions for the function.  

Each instruction list has the following five components:

- adjusted line number: index position in the bytecode list
- instruction opcode number: opcode from the bytecode list
- opname: symbolic name for the opcode
- index: if the opcode takes an argument, the numeric index value, else None
- argument: if the opcode takes an argument, the value of the argument, else None

In [38]:
import hw5a
hw5a.makeobj(s1)

{'names': ('a',),
 'consts': (None, 1),
 'code': b'd\x01}\x00|\x00S\x00',
 'instructions': [(0, 100, 'LOAD_CONST', 1, 1),
  (2, 125, 'STORE_FAST', 0, 'a'),
  (4, 124, 'LOAD_FAST', 0, 'a'),
  (6, 83, 'RETURN_VALUE', None, None)]}

Note that <code>makeobj</code> is similar to <code>dis.dis()</code>.  You may use <code>dis.dis()</code> 
to help test your implementation of <code>makeobj()</code>.

You may also want to use <code>dis.HAVE_ARGUMENT</code> to identify those
opcodes that do and do not take an argument and <code>dis.hascompare</code> to process comparison operators. <code>dis.get_instructions(f)</code> is very useful.

In [40]:
list(dis.get_instructions(s1))

[Instruction(opname='LOAD_CONST', opcode=100, arg=1, argval=1, argrepr='1', offset=0, starts_line=2, is_jump_target=False),
 Instruction(opname='STORE_FAST', opcode=125, arg=0, argval='a', argrepr='a', offset=2, starts_line=None, is_jump_target=False),
 Instruction(opname='LOAD_FAST', opcode=124, arg=0, argval='a', argrepr='a', offset=4, starts_line=3, is_jump_target=False),
 Instruction(opname='RETURN_VALUE', opcode=83, arg=None, argval=None, argrepr='', offset=6, starts_line=None, is_jump_target=False)]

In [41]:
for x in dis.get_instructions(s1):
    print (x)

Instruction(opname='LOAD_CONST', opcode=100, arg=1, argval=1, argrepr='1', offset=0, starts_line=2, is_jump_target=False)
Instruction(opname='STORE_FAST', opcode=125, arg=0, argval='a', argrepr='a', offset=2, starts_line=None, is_jump_target=False)
Instruction(opname='LOAD_FAST', opcode=124, arg=0, argval='a', argrepr='a', offset=4, starts_line=3, is_jump_target=False)
Instruction(opname='RETURN_VALUE', opcode=83, arg=None, argval=None, argrepr='', offset=6, starts_line=None, is_jump_target=False)


In [42]:
x = list(dis.get_instructions(s1))

In [43]:
x[0][0]

'LOAD_CONST'

### The Interpreter Class

We shall now implement an Interpreter class, along the lines
of the reading, which describes a full implementation of the PVM
and has the source code available on <a target=rr href="https://github.com/nedbat/byterun">github</a>.  We encourage you to
avail yourself of that resource.  Our implementation is more modest.
Nevertheless, you should try to borrow as much as possible from
"byterun" implementation.  Yes, I am telling you to copy / adapt
code from the byterun github file.

We first define a test function that will execute a Python function
using the Interpreter class.

In [44]:
def doit(func, debug=True):
    interpreter = Interpreter(debug)
    return interpreter.execute(func)

### Problem 3 - binary arithmetic

Next we define a bunch of test functions for the Interpreter

In [45]:
def s3():
    a = 1
    return a + 1

In [46]:
hw5a.doit(s3)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 124, 'LOAD_FAST', 0, 'a') 
(6, 100, 'LOAD_CONST', 1, 1) 
(8, 23, 'BINARY_ADD', None, None) 
(10, 83, 'RETURN_VALUE', None, None) 


2

In [47]:
def s3a():
    a = 1
    b = 2
    return (a + b)

In [48]:
hw5a.doit(s3a)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 100, 'LOAD_CONST', 2, 2) 
(6, 125, 'STORE_FAST', 1, 'b') 
(8, 124, 'LOAD_FAST', 0, 'a') 
(10, 124, 'LOAD_FAST', 1, 'b') 
(12, 23, 'BINARY_ADD', None, None) 
(14, 83, 'RETURN_VALUE', None, None) 


3

In [49]:
def s3b():
    a = 1
    b = 2
    return (a - b)

In [50]:
hw5a.doit(s3b)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 100, 'LOAD_CONST', 2, 2) 
(6, 125, 'STORE_FAST', 1, 'b') 
(8, 124, 'LOAD_FAST', 0, 'a') 
(10, 124, 'LOAD_FAST', 1, 'b') 
(12, 24, 'BINARY_SUBTRACT', None, None) 
(14, 83, 'RETURN_VALUE', None, None) 


-1

In [51]:
def s3c():
    a = 2
    b = 3
    return (a ** b)

In [52]:
hw5a.doit(s3c)

(0, 100, 'LOAD_CONST', 1, 2) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 100, 'LOAD_CONST', 2, 3) 
(6, 125, 'STORE_FAST', 1, 'b') 
(8, 124, 'LOAD_FAST', 0, 'a') 
(10, 124, 'LOAD_FAST', 1, 'b') 
(12, 19, 'BINARY_POWER', None, None) 
(14, 83, 'RETURN_VALUE', None, None) 


8

In [53]:
def s3d():
    a = 2
    b = 3
    return (a * b)

In [54]:
hw5a.doit(s3d)

(0, 100, 'LOAD_CONST', 1, 2) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 100, 'LOAD_CONST', 2, 3) 
(6, 125, 'STORE_FAST', 1, 'b') 
(8, 124, 'LOAD_FAST', 0, 'a') 
(10, 124, 'LOAD_FAST', 1, 'b') 
(12, 20, 'BINARY_MULTIPLY', None, None) 
(14, 83, 'RETURN_VALUE', None, None) 


6

In [55]:
def s3e():
    a = 6
    b = 3
    return (a / b)

In [56]:
hw5a.doit(s3e)

(0, 100, 'LOAD_CONST', 1, 6) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 100, 'LOAD_CONST', 2, 3) 
(6, 125, 'STORE_FAST', 1, 'b') 
(8, 124, 'LOAD_FAST', 0, 'a') 
(10, 124, 'LOAD_FAST', 1, 'b') 
(12, 27, 'BINARY_TRUE_DIVIDE', None, None) 
(14, 83, 'RETURN_VALUE', None, None) 


2.0

In [57]:
def s3f():
    a = 7
    b = 3
    return (a // b)

In [58]:
hw5a.doit(s3f)

(0, 100, 'LOAD_CONST', 1, 7) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 100, 'LOAD_CONST', 2, 3) 
(6, 125, 'STORE_FAST', 1, 'b') 
(8, 124, 'LOAD_FAST', 0, 'a') 
(10, 124, 'LOAD_FAST', 1, 'b') 
(12, 26, 'BINARY_FLOOR_DIVIDE', None, None) 
(14, 83, 'RETURN_VALUE', None, None) 


2

In [59]:
def s3g():
    a = 7
    b = 3
    return (a % b)

In [60]:
hw5a.doit(s3g)

(0, 100, 'LOAD_CONST', 1, 7) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 100, 'LOAD_CONST', 2, 3) 
(6, 125, 'STORE_FAST', 1, 'b') 
(8, 124, 'LOAD_FAST', 0, 'a') 
(10, 124, 'LOAD_FAST', 1, 'b') 
(12, 22, 'BINARY_MODULO', None, None) 
(14, 83, 'RETURN_VALUE', None, None) 


1

In [61]:
def s3h():
    ''' returns string append '''
    a = "hello"
    b = " world"
    return a + b

In [62]:
hw5a.doit(s3h)

(0, 100, 'LOAD_CONST', 1, 'hello') 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 100, 'LOAD_CONST', 2, ' world') 
(6, 125, 'STORE_FAST', 1, 'b') 
(8, 124, 'LOAD_FAST', 0, 'a') 
(10, 124, 'LOAD_FAST', 1, 'b') 
(12, 23, 'BINARY_ADD', None, None) 
(14, 83, 'RETURN_VALUE', None, None) 


'hello world'

### Problem 4 - comparison operators

def s4():
    return 1 > 2

In [89]:
hw5a.doit(s4)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 100, 'LOAD_CONST', 2, 2) 
(4, 107, 'COMPARE_OP', 4, 4) >
(6, 83, 'RETURN_VALUE', None, None) 


False

In [90]:
def s4a():
    return 1 < 2

In [91]:
hw5a.doit(s4a)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 100, 'LOAD_CONST', 2, 2) 
(4, 107, 'COMPARE_OP', 0, 0) <
(6, 83, 'RETURN_VALUE', None, None) 


True

In [92]:
def s4b():
    return 1 <= 2

In [93]:
hw5a.doit(s4b)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 100, 'LOAD_CONST', 2, 2) 
(4, 107, 'COMPARE_OP', 1, 1) <=
(6, 83, 'RETURN_VALUE', None, None) 


True

In [94]:
def s4c():
    return 1 == 2

In [95]:
hw5a.doit(s4c)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 100, 'LOAD_CONST', 2, 2) 
(4, 107, 'COMPARE_OP', 2, 2) ==
(6, 83, 'RETURN_VALUE', None, None) 


False

In [96]:
def s4d():
    return 1 != 2

In [97]:
hw5a.doit(s4d)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 100, 'LOAD_CONST', 2, 2) 
(4, 107, 'COMPARE_OP', 3, 3) !=
(6, 83, 'RETURN_VALUE', None, None) 


True

In [98]:
def s4e():
    return 1 >= 2

In [99]:
hw5a.doit(s4e)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 100, 'LOAD_CONST', 2, 2) 
(4, 107, 'COMPARE_OP', 5, 5) >=
(6, 83, 'RETURN_VALUE', None, None) 


False

### Problem 5 - jump operators

In [100]:
def s5():
    a = 1
    if a > 2:
        return 1
    else:
        return 2

In [101]:
hw5a.doit(s5)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 124, 'LOAD_FAST', 0, 'a') 
(6, 100, 'LOAD_CONST', 2, 2) 
(8, 107, 'COMPARE_OP', 4, 4) >
(10, 114, 'POP_JUMP_IF_FALSE', 16, 16) 
(16, 100, 'LOAD_CONST', 2, 2) 
(18, 83, 'RETURN_VALUE', None, None) 


2

In [102]:
def s5a():
    a = 1
    if a == 2:
        return 1
    else:
        return 2

In [103]:
hw5a.doit(s5a)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 124, 'LOAD_FAST', 0, 'a') 
(6, 100, 'LOAD_CONST', 2, 2) 
(8, 107, 'COMPARE_OP', 2, 2) ==
(10, 114, 'POP_JUMP_IF_FALSE', 16, 16) 
(16, 100, 'LOAD_CONST', 2, 2) 
(18, 83, 'RETURN_VALUE', None, None) 


2

### Problem 6 - lists, tuples, sets, subscript

In [104]:
def s6():
    ''' returns tuple '''
    a = 2
    b = a << a
    return b, b % 2

In [105]:
hw5a.doit(s6)

(0, 100, 'LOAD_CONST', 1, 2) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 124, 'LOAD_FAST', 0, 'a') 
(6, 124, 'LOAD_FAST', 0, 'a') 
(8, 62, 'BINARY_LSHIFT', None, None) 
(10, 125, 'STORE_FAST', 1, 'b') 
(12, 124, 'LOAD_FAST', 1, 'b') 
(14, 124, 'LOAD_FAST', 1, 'b') 
(16, 100, 'LOAD_CONST', 1, 2) 
(18, 22, 'BINARY_MODULO', None, None) 
(20, 102, 'BUILD_TUPLE', 2, 2) 
(22, 83, 'RETURN_VALUE', None, None) 


(8, 0)

In [106]:
def s6a():
    ''' returns list '''
    b = 5
    return [b, b % 2]


In [107]:
hw5a.doit(s6a)

(0, 100, 'LOAD_CONST', 1, 5) 
(2, 125, 'STORE_FAST', 0, 'b') 
(4, 124, 'LOAD_FAST', 0, 'b') 
(6, 124, 'LOAD_FAST', 0, 'b') 
(8, 100, 'LOAD_CONST', 2, 2) 
(10, 22, 'BINARY_MODULO', None, None) 
(12, 103, 'BUILD_LIST', 2, 2) 
(14, 83, 'RETURN_VALUE', None, None) 


[5, 1]

In [108]:
def s6b():
    ''' returns set '''
    b = 9
    return {b, b % 2}

In [109]:
hw5a.doit(s6b)

(0, 100, 'LOAD_CONST', 1, 9) 
(2, 125, 'STORE_FAST', 0, 'b') 
(4, 124, 'LOAD_FAST', 0, 'b') 
(6, 124, 'LOAD_FAST', 0, 'b') 
(8, 100, 'LOAD_CONST', 2, 2) 
(10, 22, 'BINARY_MODULO', None, None) 
(12, 104, 'BUILD_SET', 2, 2) 
(14, 83, 'RETURN_VALUE', None, None) 


{1, 9}

In [110]:
def s6c():
    ''' returns list subscript '''
    a = [1,2,3]
    return a[1]

In [111]:
hw5a.doit(s6c)

(0, 103, 'BUILD_LIST', 0, 0) 
(2, 100, 'LOAD_CONST', 1, (1, 2, 3)) 
(4, 162, 'LIST_EXTEND', 1, 1) 
(6, 125, 'STORE_FAST', 0, 'a') 
(8, 124, 'LOAD_FAST', 0, 'a') 
(10, 100, 'LOAD_CONST', 2, 1) 
(12, 25, 'BINARY_SUBSCR', None, None) 
(14, 83, 'RETURN_VALUE', None, None) 


2

### Problem 7 - slices

In [112]:
def s7():
    ''' returns list slice '''
    a = [1,2,3,4,5,6]
    return a[2:-1], a[2:4]

In [113]:
hw5a.doit(s7)

(0, 103, 'BUILD_LIST', 0, 0) 
(2, 100, 'LOAD_CONST', 1, (1, 2, 3, 4, 5, 6)) 
(4, 162, 'LIST_EXTEND', 1, 1) 
(6, 125, 'STORE_FAST', 0, 'a') 
(8, 124, 'LOAD_FAST', 0, 'a') 
(10, 100, 'LOAD_CONST', 2, 2) 
(12, 100, 'LOAD_CONST', 3, -1) 
(14, 133, 'BUILD_SLICE', 2, 2) 
(16, 25, 'BINARY_SUBSCR', None, None) 
(18, 124, 'LOAD_FAST', 0, 'a') 
(20, 100, 'LOAD_CONST', 2, 2) 
(22, 100, 'LOAD_CONST', 4, 4) 
(24, 133, 'BUILD_SLICE', 2, 2) 
(26, 25, 'BINARY_SUBSCR', None, None) 
(28, 102, 'BUILD_TUPLE', 2, 2) 
(30, 83, 'RETURN_VALUE', None, None) 


((3, 4, 5), (3, 4))

Error: should return lists, not tuples.

In [114]:
def s7a():
    ''' returns string slice '''
    a = "hello world"
    return a[3:-1]

In [115]:
hw5a.doit(s7a)

(0, 100, 'LOAD_CONST', 1, 'hello world') 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 124, 'LOAD_FAST', 0, 'a') 
(6, 100, 'LOAD_CONST', 2, 3) 
(8, 100, 'LOAD_CONST', 3, -1) 
(10, 133, 'BUILD_SLICE', 2, 2) 
(12, 25, 'BINARY_SUBSCR', None, None) 
(14, 83, 'RETURN_VALUE', None, None) 


'lo worl'

In [116]:
def s7b():
    ''' returns dictionary '''
    a = 2
    b = a ** 2
    d = {}
    d[a] = b
    return d

In [117]:
hw5a.doit(s7b)

(0, 100, 'LOAD_CONST', 1, 2) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 124, 'LOAD_FAST', 0, 'a') 
(6, 100, 'LOAD_CONST', 1, 2) 
(8, 19, 'BINARY_POWER', None, None) 
(10, 125, 'STORE_FAST', 1, 'b') 
(12, 105, 'BUILD_MAP', 0, 0) 
(14, 125, 'STORE_FAST', 2, 'd') 
(16, 124, 'LOAD_FAST', 1, 'b') 
(18, 124, 'LOAD_FAST', 2, 'd') 
(20, 124, 'LOAD_FAST', 0, 'a') 
(22, 60, 'STORE_SUBSCR', None, None) 
(24, 124, 'LOAD_FAST', 2, 'd') 
(26, 83, 'RETURN_VALUE', None, None) 


{2: 4}

In [118]:
def s7c():
    ''' dict access '''
    x = {}
    x['a'] = 1
    y = x['a']
    return y

In [119]:
hw5a.doit(s7c)

(0, 105, 'BUILD_MAP', 0, 0) 
(2, 125, 'STORE_FAST', 0, 'x') 
(4, 100, 'LOAD_CONST', 1, 1) 
(6, 124, 'LOAD_FAST', 0, 'x') 
(8, 100, 'LOAD_CONST', 2, 'a') 
(10, 60, 'STORE_SUBSCR', None, None) 
(12, 124, 'LOAD_FAST', 0, 'x') 
(14, 100, 'LOAD_CONST', 2, 'a') 
(16, 25, 'BINARY_SUBSCR', None, None) 
(18, 125, 'STORE_FAST', 1, 'y') 
(20, 124, 'LOAD_FAST', 1, 'y') 
(22, 83, 'RETURN_VALUE', None, None) 


1

### Problem 8 - unary and inplace operators

In [120]:
def s8b():
    x = 1
    return -x

In [121]:
hw5a.doit(s8b)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 125, 'STORE_FAST', 0, 'x') 
(4, 124, 'LOAD_FAST', 0, 'x') 
(6, 11, 'UNARY_NEGATIVE', None, None) 
(8, 83, 'RETURN_VALUE', None, None) 


-1

In [122]:
def s8c():
    x = -1
    return +x

In [123]:
hw5a.doit(s8c)

(0, 100, 'LOAD_CONST', 1, -1) 
(2, 125, 'STORE_FAST', 0, 'x') 
(4, 124, 'LOAD_FAST', 0, 'x') 
(6, 10, 'UNARY_POSITIVE', None, None) 
(8, 83, 'RETURN_VALUE', None, None) 


-1

In [124]:
def s8d():
    x = 1
    return not x

In [125]:
hw5a.doit(s8d)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 125, 'STORE_FAST', 0, 'x') 
(4, 124, 'LOAD_FAST', 0, 'x') 
(6, 12, 'UNARY_NOT', None, None) 
(8, 83, 'RETURN_VALUE', None, None) 


False

In [126]:
def s8e():
    x = 1
    return ~x

In [127]:
hw5a.doit(s8e)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 125, 'STORE_FAST', 0, 'x') 
(4, 124, 'LOAD_FAST', 0, 'x') 
(6, 15, 'UNARY_INVERT', None, None) 
(8, 83, 'RETURN_VALUE', None, None) 


-2

In [128]:
def s8f():
    x = 1
    x += 10
    return x

In [129]:
hw5a.doit(s8f)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 125, 'STORE_FAST', 0, 'x') 
(4, 124, 'LOAD_FAST', 0, 'x') 
(6, 100, 'LOAD_CONST', 2, 10) 
(8, 55, 'INPLACE_ADD', None, None) 
(10, 125, 'STORE_FAST', 0, 'x') 
(12, 124, 'LOAD_FAST', 0, 'x') 
(14, 83, 'RETURN_VALUE', None, None) 


11

In [130]:
def s8g():
    x = 1
    x -= 10
    return x

In [131]:
hw5a.doit(s8g)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 125, 'STORE_FAST', 0, 'x') 
(4, 124, 'LOAD_FAST', 0, 'x') 
(6, 100, 'LOAD_CONST', 2, 10) 
(8, 56, 'INPLACE_SUBTRACT', None, None) 
(10, 125, 'STORE_FAST', 0, 'x') 
(12, 124, 'LOAD_FAST', 0, 'x') 
(14, 83, 'RETURN_VALUE', None, None) 


-9

In [132]:
def s8h():
    x = 1
    x *= 10
    return x

In [133]:
hw5a.doit(s8h)

(0, 100, 'LOAD_CONST', 1, 1) 
(2, 125, 'STORE_FAST', 0, 'x') 
(4, 124, 'LOAD_FAST', 0, 'x') 
(6, 100, 'LOAD_CONST', 2, 10) 
(8, 57, 'INPLACE_MULTIPLY', None, None) 
(10, 125, 'STORE_FAST', 0, 'x') 
(12, 124, 'LOAD_FAST', 0, 'x') 
(14, 83, 'RETURN_VALUE', None, None) 


10

In [134]:
def s8i():
    x = 10
    x %= 3
    return x

In [135]:
hw5a.doit(s8i)

(0, 100, 'LOAD_CONST', 1, 10) 
(2, 125, 'STORE_FAST', 0, 'x') 
(4, 124, 'LOAD_FAST', 0, 'x') 
(6, 100, 'LOAD_CONST', 2, 3) 
(8, 59, 'INPLACE_MODULO', None, None) 
(10, 125, 'STORE_FAST', 0, 'x') 
(12, 124, 'LOAD_FAST', 0, 'x') 
(14, 83, 'RETURN_VALUE', None, None) 


1

In [136]:
def s8j():
    x = 10
    x /= 3
    return x

In [137]:
hw5a.doit(s8j)

(0, 100, 'LOAD_CONST', 1, 10) 
(2, 125, 'STORE_FAST', 0, 'x') 
(4, 124, 'LOAD_FAST', 0, 'x') 
(6, 100, 'LOAD_CONST', 2, 3) 
(8, 29, 'INPLACE_TRUE_DIVIDE', None, None) 
(10, 125, 'STORE_FAST', 0, 'x') 
(12, 124, 'LOAD_FAST', 0, 'x') 
(14, 83, 'RETURN_VALUE', None, None) 


3.3333333333333335

In [138]:
def s8k():
    x = 32
    x <<= 2
    return x

In [139]:
hw5a.doit(s8k)

(0, 100, 'LOAD_CONST', 1, 32) 
(2, 125, 'STORE_FAST', 0, 'x') 
(4, 124, 'LOAD_FAST', 0, 'x') 
(6, 100, 'LOAD_CONST', 2, 2) 
(8, 75, 'INPLACE_LSHIFT', None, None) 
(10, 125, 'STORE_FAST', 0, 'x') 
(12, 124, 'LOAD_FAST', 0, 'x') 
(14, 83, 'RETURN_VALUE', None, None) 


128

In [140]:
def s8l():
    x = 32
    x >>= 2
    return x

In [141]:
hw5a.doit(s8l)

(0, 100, 'LOAD_CONST', 1, 32) 
(2, 125, 'STORE_FAST', 0, 'x') 
(4, 124, 'LOAD_FAST', 0, 'x') 
(6, 100, 'LOAD_CONST', 2, 2) 
(8, 76, 'INPLACE_RSHIFT', None, None) 
(10, 125, 'STORE_FAST', 0, 'x') 
(12, 124, 'LOAD_FAST', 0, 'x') 
(14, 83, 'RETURN_VALUE', None, None) 


8

### Problem 9 - logical binary operators

In [142]:
def s9():
    a = 2
    return a << 3

In [143]:
hw5a.doit(s9)

(0, 100, 'LOAD_CONST', 1, 2) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 124, 'LOAD_FAST', 0, 'a') 
(6, 100, 'LOAD_CONST', 2, 3) 
(8, 62, 'BINARY_LSHIFT', None, None) 
(10, 83, 'RETURN_VALUE', None, None) 


16

In [144]:
def s9a():
    a = 19
    return a >> 3

In [145]:
hw5a.doit(s9a)

(0, 100, 'LOAD_CONST', 1, 19) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 124, 'LOAD_FAST', 0, 'a') 
(6, 100, 'LOAD_CONST', 2, 3) 
(8, 63, 'BINARY_RSHIFT', None, None) 
(10, 83, 'RETURN_VALUE', None, None) 


2

In [146]:
def s9b():
    a = 19
    return a & 3

In [147]:
hw5a.doit(s9b)

(0, 100, 'LOAD_CONST', 1, 19) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 124, 'LOAD_FAST', 0, 'a') 
(6, 100, 'LOAD_CONST', 2, 3) 
(8, 64, 'BINARY_AND', None, None) 
(10, 83, 'RETURN_VALUE', None, None) 


3

In [148]:
def s9c():
    a = 19
    return a | 3

In [149]:
hw5a.doit(s9c)

(0, 100, 'LOAD_CONST', 1, 19) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 124, 'LOAD_FAST', 0, 'a') 
(6, 100, 'LOAD_CONST', 2, 3) 
(8, 66, 'BINARY_OR', None, None) 
(10, 83, 'RETURN_VALUE', None, None) 


19

In [150]:
def s9d():
    a = 19
    return a ^ 3

In [151]:
hw5a.doit(s9d)

(0, 100, 'LOAD_CONST', 1, 19) 
(2, 125, 'STORE_FAST', 0, 'a') 
(4, 124, 'LOAD_FAST', 0, 'a') 
(6, 100, 'LOAD_CONST', 2, 3) 
(8, 65, 'BINARY_XOR', None, None) 
(10, 83, 'RETURN_VALUE', None, None) 


16

### Extra binary operators

In [152]:
# binary in
def s10():
    a = [1,2,3,4,5,6]
    b = 4
    if b in a:
        return "yes"
    else:
        return "no"

In [153]:
hw5a.doit(s10)

(0, 103, 'BUILD_LIST', 0, 0) 
(2, 100, 'LOAD_CONST', 1, (1, 2, 3, 4, 5, 6)) 
(4, 162, 'LIST_EXTEND', 1, 1) 
(6, 125, 'STORE_FAST', 0, 'a') 
(8, 100, 'LOAD_CONST', 2, 4) 
(10, 125, 'STORE_FAST', 1, 'b') 
(12, 124, 'LOAD_FAST', 1, 'b') 
(14, 124, 'LOAD_FAST', 0, 'a') 
(16, 118, 'CONTAINS_OP', 0, 0) 
(18, 114, 'POP_JUMP_IF_FALSE', 24, 24) 
(20, 100, 'LOAD_CONST', 3, 'yes') 
(22, 83, 'RETURN_VALUE', None, None) 


'yes'

In [154]:
def s10a():
    a = [1,2,3,4,5,6]
    b = 4
    if b not in a:
        return "yes"
    else:
        return "no"

In [155]:
hw5a.doit(s10a)

(0, 103, 'BUILD_LIST', 0, 0) 
(2, 100, 'LOAD_CONST', 1, (1, 2, 3, 4, 5, 6)) 
(4, 162, 'LIST_EXTEND', 1, 1) 
(6, 125, 'STORE_FAST', 0, 'a') 
(8, 100, 'LOAD_CONST', 2, 4) 
(10, 125, 'STORE_FAST', 1, 'b') 
(12, 124, 'LOAD_FAST', 1, 'b') 
(14, 124, 'LOAD_FAST', 0, 'a') 
(16, 118, 'CONTAINS_OP', 1, 1) 
(18, 114, 'POP_JUMP_IF_FALSE', 24, 24) 
(24, 100, 'LOAD_CONST', 4, 'no') 
(26, 83, 'RETURN_VALUE', None, None) 


'no'

In [156]:
# binary is
def s10b():
    a = [1,2,3,4,5,6]
    b = 4
    if b is a:
        return "yes"
    else:
        return "no"

In [157]:
hw5a.doit(s10b)

(0, 103, 'BUILD_LIST', 0, 0) 
(2, 100, 'LOAD_CONST', 1, (1, 2, 3, 4, 5, 6)) 
(4, 162, 'LIST_EXTEND', 1, 1) 
(6, 125, 'STORE_FAST', 0, 'a') 
(8, 100, 'LOAD_CONST', 2, 4) 
(10, 125, 'STORE_FAST', 1, 'b') 
(12, 124, 'LOAD_FAST', 1, 'b') 
(14, 124, 'LOAD_FAST', 0, 'a') 
(16, 117, 'IS_OP', 0, 0) 
(18, 114, 'POP_JUMP_IF_FALSE', 24, 24) 
(24, 100, 'LOAD_CONST', 4, 'no') 
(26, 83, 'RETURN_VALUE', None, None) 


'no'

In [158]:
def s10c():
    a = [1,2,3,4,5,6]
    b = 4
    if b is not a:
        return "yes"
    else:
        return "no"

In [159]:
hw5a.doit(s10c)

(0, 103, 'BUILD_LIST', 0, 0) 
(2, 100, 'LOAD_CONST', 1, (1, 2, 3, 4, 5, 6)) 
(4, 162, 'LIST_EXTEND', 1, 1) 
(6, 125, 'STORE_FAST', 0, 'a') 
(8, 100, 'LOAD_CONST', 2, 4) 
(10, 125, 'STORE_FAST', 1, 'b') 
(12, 124, 'LOAD_FAST', 1, 'b') 
(14, 124, 'LOAD_FAST', 0, 'a') 
(16, 117, 'IS_OP', 1, 1) 
(18, 114, 'POP_JUMP_IF_FALSE', 24, 24) 
(20, 100, 'LOAD_CONST', 3, 'yes') 
(22, 83, 'RETURN_VALUE', None, None) 


'yes'

### Define the Interpreter Class

Now we start to define the Interpreter itself.

The PVM uses a stack to control execution and pass arguments to functions
and operators.
- The result instance variable will contain the value returned by the function.
- The debug flag is used to turn on debugging output.
- The environment instance variable is a dictionary 
containing variable bindings.
- The pc instance variable is the program counter.

In [160]:
class Interpreter:
    def __init__(self, debug = True):
        self.stack = []
        self.result = None
        self.debug = debug
        self.environment = {}
        self.pc = 0

The execute method controls the action.
It first decodes the function using <code>makeobj()</code> which we defined above.
It sets the program counter (pc) to 0.  If the <code>pc</code> becomes
greater than the number of instructions, the program halts.

<code>execute</code> cycles through the instructions, printing them out if debug is True.
Each PVM opcode/opname is defined as a method of the <code>Interpreter</code> class.
This means that each opname is an attribute of the class and 
can be accessed using <code>getattr(self, instruction)</code>.  The 
opcode method is called with or without an argument, as appropriate.

When the <code>while()</code> loop finishes, execute returns the result.

In [161]:

    def execute(self, func):
        codedict = makeobj(func)
        self.instructions = codedict["instructions"]
        self.pc = 0
        while (self.pc < len(self.instructions)):
            each_step = self.instructions[self.pc]
            ## if debug, print out symbol for comparison operator
            if self.debug: 
                suffix = ''
                if each_step[2] == 'COMPARE_OP':
                    suffix = self.COMPARE_OPERATORS_SYMBOLS[each_step[3]]
                print (each_step, suffix)

            self.pc += 1
            lineno, inst, instruction, index, argument = each_step
            bytecode_method = getattr(self, instruction)
            if argument is None:
                bytecode_method()
            else:
                bytecode_method(argument)
        return self.result

Note that execute calls <code>makeobj()</code> defined above.
If your <code>makeobj</code> function is not working correctly, you can still
debug your execute function by importing the bytecode version of 
<code>makeobj</code> from <code>hw5a.pyc</code>:
<pre>
from hw5a import makeobj
</pre>
We define a few stack operations that are used in implementing 
the opcode methods.

In [162]:

    def top(self):
        return self.stack[-1]

    def pop(self):
        return self.stack.pop()

    def push(self, *vals):
        self.stack.extend(vals)

    def popn(self, n):
        """Pop a number of values from the value stack.
        A list of `n` values is returned, the deepest value first.
        """
        if n:
            ret = self.stack[-n:]
            self.stack[-n:] = []
            return ret
        else:
            return []


We first implement the opcodes needed to execute function <code>s1()</code>.
Write the following methods:

In [163]:

    def STORE_FAST(self, name):
        val = self.stack.pop()
        self.environment[name] = val

    def LOAD_FAST(self, name):
        pass

    def LOAD_CONST(self, number):
        pass

    ## set result from stack
    ## set pc to be out of range and thereby halt.
    def RETURN_VALUE(self):
        pass

### ** problem 3 ** (10 points)

Define the following set of binary operators needed to 
execute the s3 set of functions.

In [164]:

    def BINARY_ADD(self):
        pass

    def BINARY_SUBTRACT(self):
        pass

    def BINARY_POWER(self):
        pass

    def BINARY_MULTIPLY(self):
        pass

    def BINARY_DIVIDE(self):
        pass

    ## same as divide for Python 3, ich glaube.
    def BINARY_TRUE_DIVIDE(self):
        pass

    def BINARY_FLOOR_DIVIDE(self):
        pass

    def BINARY_MODULO(self):
        pass


### ** problem 4 ** (10 points)

Define the set of comparison operators needed to 
execute the s4 set of functions.

In [165]:

    ## comparison operators
    ## -----------------------------------
    COMPARE_OPERATORS_SYMBOLS = [
        '<', '<=', '==', '!=', '>', '>=', 'in', 'not in', 'is', 'is not', 'subclass']


    COMPARE_OPERATORS = [
        operator.lt,
        operator.le,
        operator.eq,
        operator.ne,
        operator.gt,
        operator.ge,
        lambda x, y: x in y,
        lambda x, y: x not in y,
        lambda x, y: x is y,
        lambda x, y: x is not y,
        lambda x, y: issubclass(x, Exception) and issubclass(x, y),
    ]

    def COMPARE_OP(self, opnum):
        pass


### ** problem 5 ** (10 points)

Define the set of jump operators needed to 
execute the s5 set of functions.  Some are given.

In [166]:

    ## jumps
    ## -----------------------------------
    ## This method is called by the other jump methods.
    ## It causes the given address to be the next 
    ## instruction to execute
    def jump(self, address):
        pass

    def JUMP_FORWARD(self, jump):
        self.jump(jump)

    def JUMP_ABSOLUTE(self, jump):
        self.jump(jump)

    def JUMP_IF_TRUE(self, jump):
        pass

    def JUMP_IF_FALSE(self, jump):
        pass

    def POP_JUMP_IF_FALSE(self, jump):
        pass

    def JUMP_IF_TRUE_OR_POP(self, jump):
        pass

    def JUMP_IF_FALSE_OR_POP(self, jump):
        pass


### ** problem 6 ** (10 points)

Define the set of operators needed to build and index
lists, tuples, and sets, and execute the s6 set of functions.

In [167]:

    def BUILD_TUPLE(self, count):
        pass

    def BUILD_LIST(self, count):
        pass

    def BUILD_SET(self, count):
        pass

    def BINARY_SUBSCR(self):
        pass

    ### new bytecode in 3.9
    def LIST_EXTEND(self,count):
        elts = self.popn(2)
        self.push(elts[count])


### ** problem 7 ** (10 points)

Define the set of operators needed to implement the slice function
and define the set of operators needed to implement dictionaries
and execute the s7 set of functions. 

In [168]:
    def BUILD_SLICE(self, count):
        pass

    def BUILD_MAP(self, size):
        pass

    def STORE_MAP(self):
        pass

    def STORE_SUBSCR(self):
        pass

### ** problem 8 ** (10 points)

Define the set of operators to implement unary and inplace functions
and execute the s8 set of functions.

In [169]:

    def UNARY_POSITIVE(self):
        pass

    def UNARY_NEGATIVE(self):
        pass

    def UNARY_NOT(self):
        pass

    def UNARY_INVERT(self):
        pass

    def INPLACE_ADD(self):
        pass

    def INPLACE_SUBTRACT(self):
        pass

    def INPLACE_MULTIPLY(self):
        pass

    def INPLACE_TRUE_DIVIDE(self):
        pass

    def INPLACE_MODULO(self):
        pass

    def INPLACE_LSHIFT(self):
        pass

    def INPLACE_RSHIFT(self):
        pass

### ** problem 9 ** (10 points)

Define the set of operators needed to implement the logical binary
operators and execute the s9 set of functions.

In [172]:


    ## binary operators
    ## -----------------------------------

    def BINARY_LSHIFT(self):
        pass

    def BINARY_RSHIFT(self):
        pass

    def BINARY_AND(self):
        pass

    def BINARY_XOR(self):
        pass

    def BINARY_OR(self):
        pass
    
    ### problem 10
### new bytecode in 3.9
    def CONTAINS_OP(self,flag):
        if flag:
            self.COMPARE_OP(7)
        else:
            self.COMPARE_OP(6)
            
### new bytecode in 3.9
    def IS_OP(self,flag):
        if flag:
            self.COMPARE_OP(9)
        else:
            self.COMPARE_OP(8)